In [1]:
%matplotlib inline

In [2]:
import spikeinterface.full as si
import spikeinterface.preprocessing as spre

import numpy as np
import matplotlib.pyplot as plt
from pathlib import Path
import mountainsort5 as ms5

C:\Users\Harris_Lab\miniconda3\envs\si_env\lib\site-packages\tridesclous\numba_tools.py:11: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @jit(parallel=True)
C:\Users\Harris_Lab\miniconda3\envs\si_env\lib\site-packages\tridesclous\numba_tools.py:33: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @jit(parallel=True)
C:\Users\Harris_Lab\miniconda3\envs\si_env\lib\s

In [8]:
base_folder = Path(r'C:\Users\Harris_Lab\Projects\burst-detector\data\neuropixels_dohoung')

In [3]:
base_folder = Path(r'C:\Users\Harris_Lab\Projects\burst-detector\data\neuropixels_dohoung')
spikeglx_folder = base_folder / 'ANM480363_20210527_pfc320_hpc180_g0'

stream_names, stream_ids = si.get_neo_streams('spikeglx', spikeglx_folder)
recording = si.read_spikeglx(spikeglx_folder, stream_name='imec1.ap', load_sync_channel=False)
recording = si.concatenate_recordings([recording])

In [4]:
recording_filtered = spre.bandpass_filter(recording, freq_min=300, freq_max=6000)
recording_preprocessed: si.BaseRecording = spre.whiten(recording_filtered, dtype='float32')
    
rec = recording_preprocessed.save(folder=r'C:\Users\Harris_Lab\Projects\burst-detector\data\neuropixels_dohoung\ms5\record',n_jobs=-1)

write_binary_recording with n_jobs = 24 and chunk_size = 30000


write_binary_recording:   0%|          | 0/2463 [00:00<?, ?it/s]

In [5]:
rec.annotate(is_filtered=True)
rec._kwargs['file_paths'] = [r'C:\Users\Harris_Lab\Projects\burst-detector\data\neuropixels_dohoung\ms5\record\traces_cached_seg0.raw']
sorting = ms5.sorting_scheme2(
    rec,
    sorting_parameters=ms5.Scheme2SortingParameters(
        phase1_detect_channel_radius=150,
        detect_channel_radius=50,
        training_duration_sec=120,
        detect_sign=0,
#         detect_threshold=3.5,
#         phase1_detect_threshold=3.5
    ),
)

Number of channels: 384
Number of timepoints: 3600000
Sampling frequency: 30000.0 Hz
Channel 0: [0. 0.]
Channel 1: [32.  0.]
Channel 2: [ 0. 15.]
Channel 3: [32. 15.]
Channel 4: [ 0. 30.]
Channel 5: [32. 30.]
Channel 6: [ 0. 45.]
Channel 7: [32. 45.]
Channel 8: [ 0. 60.]
Channel 9: [32. 60.]
Channel 10: [ 0. 75.]
Channel 11: [32. 75.]
Channel 12: [ 0. 90.]
Channel 13: [32. 90.]
Channel 14: [  0. 105.]
Channel 15: [ 32. 105.]
Channel 16: [  0. 120.]
Channel 17: [ 32. 120.]
Channel 18: [  0. 135.]
Channel 19: [ 32. 135.]
Channel 20: [  0. 150.]
Channel 21: [ 32. 150.]
Channel 22: [  0. 165.]
Channel 23: [ 32. 165.]
Channel 24: [  0. 180.]
Channel 25: [ 32. 180.]
Channel 26: [  0. 195.]
Channel 27: [ 32. 195.]
Channel 28: [  0. 210.]
Channel 29: [ 32. 210.]
Channel 30: [  0. 225.]
Channel 31: [ 32. 225.]
Channel 32: [  0. 240.]
Channel 33: [ 32. 240.]
Channel 34: [  0. 255.]
Channel 35: [ 32. 255.]
Channel 36: [  0. 270.]
Channel 37: [ 32. 270.]
Channel 38: [  0. 285.]
Channel 39: [ 32. 2

In [6]:
sorting = sorting.save(folder=base_folder / 'ms5/sorting', n_jobs=20)

In [10]:
we = si.extract_waveforms(rec, sorting, folder=base_folder / 'ms5/waveforms',
                          sparse=True, max_spikes_per_unit=1000, ms_before=1.5,ms_after=2.)

extract waveforms shared_memory:   0%|          | 0/2463 [00:00<?, ?it/s]

extract waveforms memmap:   0%|          | 0/2463 [00:00<?, ?it/s]

In [3]:
# rec = si.load_extractor(r'C:\Users\Harris_Lab\Projects\burst-detector\data\neuropixels_dohoung\ms5\record')
# sorting = si.load_extractor(r'C:\Users\Harris_Lab\Projects\burst-detector\data\neuropixels_dohoung\ms5\sorting')
# we = si.load_waveforms(r'C:\Users\Harris_Lab\Projects\burst-detector\data\neuropixels_dohoung\ms5\waveform')

In [12]:
phy_folder = r'C:\Users\Harris_Lab\Projects\burst-detector\data\neuropixels_dohoung\ms5\phy'

si.export_to_phy(waveform_extractor=we, output_folder=phy_folder, verbose=False, copy_binary=False)


C:\Users\Harris_Lab\miniconda3\envs\si_env\lib\site-packages\spikeinterface\exporters\to_phy.py:61: UserWarning: Exporting to Phy with many channels and without sparsity might result in a heavy and less informative visualization. You can use use a sparse WaveformExtractor or you can use the 'sparsity' argument to enforce sparsity (see compute_sparsity())
  warnings.warn(


extract amplitudes:   0%|          | 0/2463 [00:00<?, ?it/s]

In [11]:
we.recording._kwargs

{'folder_path': 'C:\\Users\\Harris_Lab\\Projects\\burst-detector\\data\\neuropixels_dohoung\\ms5\\record',
 'file_paths': ['C:\\Users\\Harris_Lab\\Projects\\burst-detector\\data\\neuropixels_dohoung\\ms5\\record\\traces_cached_seg0.raw']}